In [ ]:
import pandas as pd
import numpy as np

In [ ]:
feature_df = pd.read_excel('/home/amin/thesis/src/Step/Feature_selection_RF/RFC_کنور.xlsx')

In [ ]:
data = pd.read_excel('/home/amin/thesis/src/data/MAIN-FILES/FINNAL_DATA/کنور.xlsx')

In [ ]:
data.drop(columns=['تاریخ شمسی'], inplace=True)

In [ ]:
df = data.resample('M', on='Date').mean()

In [ ]:
df.head()

In [ ]:
df.columns.to_list()

In [ ]:
def classify_return(return_value):
    if return_value > 5:
        return 'Above +5'
    elif 2.5 < return_value <= 5:
        return '+2.5 to +5'
    elif 0 <= return_value <= 2.5:
        return '+0 to +2.5'
    elif -5 <= return_value < 0:
        return '0 to -5'
    else:
        return 'Below -5'


In [ ]:
pct_price = df['پایانی*سهم*'].pct_change() * 100

In [ ]:
df['Return_Class'] = pct_price.apply(classify_return)


In [ ]:
df.head()

In [ ]:
from sklearn.preprocessing import LabelEncoder

In [ ]:
df['Return_Class']  = LabelEncoder().fit_transform(df['Return_Class'])


In [ ]:
df['Shifted_Return_Class'] = df['Return_Class'].shift(periods=1).fillna(0)


In [ ]:
monthly_features = feature_df.iloc[-1]

In [ ]:
monthly_features

In [ ]:
from sklearn.model_selection import StratifiedKFold
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import accuracy_score, confusion_matrix, classification_report
from sklearn.preprocessing import StandardScaler

# Function to classify return

In [ ]:
import os
import warnings

import numpy as np
import pandas as pd
from sklearn.model_selection import  train_test_split
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.svm import SVC
from sklearn.metrics import accuracy_score, confusion_matrix, classification_report
from sklearn.metrics import precision_recall_fscore_support


warnings.filterwarnings('ignore')

In [ ]:
feature_df = pd.read_excel('/home/amin/thesis/src/Step/Feature_selection_RF/RFC_کنور.xlsx')
data = pd.read_excel('/home/amin/thesis/src/data/MAIN-FILES/FINNAL_DATA/کنور.xlsx')



data.drop(columns=['تاریخ شمسی'], inplace=True)


monthly_features = feature_df.iloc[-1]
df = data.resample('M', on='Date').mean()

In [ ]:
monthly_features.head()

# K Fold 

In [ ]:

def return_classifier(df) :
    def classify_return(return_value):
        if return_value > 5:
            return 'Above +5'
        elif 2.5 < return_value <= 5:
            return '+2.5 to +5'
        elif 0 <= return_value <= 2.5:
            return '+0 to +2.5'
        elif -5 <= return_value < 0:
            return '0 to -5'
        else:
            return 'Below -5'
    

    

    pct_price = df['پایانی*سهم*'].pct_change() * 100
    df['Return_Class'] = pct_price.apply(classify_return)
    df['Return_Class']  = LabelEncoder().fit_transform(df['Return_Class'])
    df['Shifted_Return_Class'] = df['Return_Class'].shift(periods=1).fillna(0)

    scaling = StandardScaler()

    # Select numeric columns except the target column
    numeric_columns = df.select_dtypes(include=[np.number]).drop(columns=['Return_Class']).columns.tolist()
    # Extract the subset of data with only numeric columns
    num_data = df[numeric_columns]

    y_df = df['Return_Class']
    X_df = scaling.fit_transform(num_data)


    acc_log = []
    precision_log = []
    recall_log = []
    f1_log = []

    kf = StratifiedKFold(n_splits=5)
    for fold, (train_idx, test_idx) in enumerate(kf.split(X=X_df, y=y_df)):
        X_train, X_test = df.iloc[train_idx, :-1], df.iloc[test_idx,:-1]
        y_train, y_test = df.iloc[train_idx, -1], df.iloc[test_idx, -1]

        scaler = StandardScaler()
        X_train = scaler.fit_transform(X_train)
        X_test = scaler.transform(X_test)

        model = SVC()
        model.fit(X_train, y_train)
        y_pred = model.predict(X_test)
        acc = accuracy_score(y_test, y_pred)
        acc_log.append(acc)

        precision, recall, f1, _ = precision_recall_fscore_support(y_test, y_pred, average= 'macro')

        precision_log.append(precision)
        recall_log.append(recall)
        f1_log.append(f1)




    accuracy = np.mean(acc_log)
    precision = np.mean(precision_log)
    recall = np.mean(recall_log)
    f1 = np.mean(f1_log)

    return accuracy, precision, recall, f1





# simple evaluation

In [ ]:

def return_classifier(df) :
    def classify_return(return_value):
        if return_value > 5:
            return 'Above +5'
        elif 2.5 < return_value <= 5:
            return '+2.5 to +5'
        elif 0 <= return_value <= 2.5:
            return '+0 to +2.5'
        elif -5 <= return_value < 0:
            return '0 to -5'
        else:
            return 'Below -5'
    

    

    pct_price = df['پایانی*سهم*'].pct_change() * 100
    df['Return_Class'] = pct_price.apply(classify_return)
    df['Return_Class']  = LabelEncoder().fit_transform(df['Return_Class'])
    df['Shifted_Return_Class'] = df['Return_Class'].shift(periods=1).fillna(0)

    scaling = StandardScaler()

    # Select numeric columns except the target column
    numeric_columns = df.select_dtypes(include=[np.number]).drop(columns=['Return_Class']).columns.tolist()
    # Extract the subset of data with only numeric columns
    num_data = df[numeric_columns]

    y_df = df['Return_Class']
    X_df = scaling.fit_transform(num_data)

     # Train-test split data
    X_train, X_test, y_train, y_test = train_test_split(X_df, y_df, test_size=0.2)


    model = SVC()
    # Fit the model
    model.fit(X_train, y_train)

    # Predict on the test set (either old or new)
    y_pred = model.predict(X_test)

    # Evaluation metrics for classification
    accuracy = accuracy_score(y_test, y_pred)
    precision, recall, f1, _ = precision_recall_fscore_support(y_test, y_pred, average= 'macro')

    return accuracy, precision,recall, f1





In [ ]:
def feature_cleaner(df, inx) :
    feat_imp = df.Features[inx].replace("[", "").replace("]", "")
    feat_imp = feat_imp.split(",")
    list_i = [ ]
    for item in feat_imp:
        list_i.append(item.replace("'", ""))
    list2 = [ ]
    for item in list_i :
        if item.startswith(' ') :
            list2.append(item[1: ])
        elif item.endswith(' ') :
            list2.append(item[:-1])
        else :
            list2.append(item)
    if 'پایانی*سهم*' not in list2 :
        list2.append('پایانی*سهم*')
    if 'پایین\\\\u200cترین*سهم*' in list2:
        list2.remove('پایین\\\\u200cترین*سهم*')

    return list2



In [ ]:
over_all_accuracy = []
over_all_precision = []
over_all_recall = []
over_all_f1 = []

In [ ]:
for inx in range(10 , len(df)) :
    new_df = df.iloc[ : inx ]
    imp_columns = feature_cleaner(monthly_features, inx)
    try:
        final_df = new_df[imp_columns]
        accuracy, precision, recall, f1 = return_classifier(final_df)
        print(f'Accuracy = {accuracy} ')
        print(f'Precision = {precision}')
        print(f'Recall = {recall}')
        print(f'F1 = {f1}')
        print('**************************')
        over_all_accuracy.append(accuracy)
        over_all_precision.append(precision)
        over_all_recall.append(recall)
        over_all_f1.append(f1)
    except KeyError :
        except_voc = 'پایین\\\\u200cترین*سهم*'
        if except_voc in imp_columns :
            imp_columns.remove(except_voc)
            final_df = new_df[imp_columns]
            accuracy, precision, recall, f1 = return_classifier(final_df)
            print(f'Accuracy = {accuracy} ')
            print(f'Precision = {precision}')
            print(f'Recall = {recall}')
            print(f'F1 = {f1}')
            print('**************************')
            over_all_accuracy.append(accuracy)
            over_all_precision.append(precision)
            over_all_recall.append(recall)
            over_all_f1.append(f1)
print(f'Accuracy = {np.mean(over_all_accuracy)}')
print(f'Precision = {np.mean(over_all_precision)}')



In [ ]:
list2 = [ ]
for item in list_i :
    if item.startswith(' ') :
        list2.append(item[1: ])
    elif item.endswith(' ') :
        list2.append(item[:-1])
    else :
        list2.append(item)

In [ ]:
monthly_features = pd.DataFrame(feature_df.iloc[-1],)
monthly_features = monthly_features.rename(columns={3: 'Features'})
monthly_features.reset_index(inplace=True)


In [ ]:
monthly_features.head()

In [ ]:
len(monthly_features.Features[0])

In [ ]:
type(monthly_features.Features[0])

In [ ]:
feat_imp = monthly_features.Features[0].replace("[", "").replace("]", "")
feat_imp = feat_imp.split(",")
feat_imp

In [ ]:
list_i = [ ]
for item in feat_imp:
    list_i.append(item.replace("'", ""))
len(list_i)
    

In [ ]:
list2 = [ ]
for item in list_i :
    if item.startswith(' ') :
        list2.append(item[1: ])
    elif item.endswith(' ') :
        list2.append(item[:-1])
    else :
        list2.append(item)



len(list2)

In [ ]:
df.columns.to_list()

In [ ]:
df.reset_index(inplace=True)
df['Date'] = pd.to_datetime(df['Date'])

In [ ]:
df[list2]

In [ ]:
df.rename(columns={'پایین\u200cترین*سهم*' : 'پایین ترین*سهم*'}, inplace=True)

In [ ]:
df["خرید حقوقی-حجم(تعداد سهام)*صنعت*"]

In [ ]:
len(feature_cleaner(monthly_features,5))

In [ ]:
for i in range(5 , 10):
    print(i)

In [ ]:
new_df555 = df.iloc[ : 55]


In [ ]:
new_df555['فروش حقیقی-ارزش(ریال)*صنعت*']

In [ ]:
accuracy, confusion, report = return_classifier(new_df555)

In [ ]:
accuracy

In [ ]:
confusion

In [ ]:
print(report)

In [ ]:
monthly_features.Features[5 + 0]

In [ ]:
imp_columns = monthly_features.Features[5 + 0].replace("[", "").replace("]", "")
imp_columns = imp_columns.split(",")
feat_list = [ ]
for item in imp_columns :
    feat_list.append(item.replace("'", ""))

In [ ]:
feat_list

In [ ]:
n = 0
for item in feat_list : 
    if item not in new_df555.columns.to_list() : 
        n += 1
n

In [ ]:
import pandas as pd
import numpy as np

In [ ]:
feature_df = pd.read_excel('/home/amin/thesis/src/Step/Feature_selection_RF/RFC_کنور.xlsx')
data = pd.read_excel('/home/amin/thesis/src/data/MAIN-FILES/FINNAL_DATA/کنور.xlsx')

In [ ]:

data.drop(columns=['تاریخ شمسی'], inplace=True)
df = data.resample('M', on='Date').mean()
df.reset_index(inplace=True)
df['Date'] = pd.to_datetime(df['Date'])


monthly_features = pd.DataFrame(feature_df.iloc[-1],)
monthly_features = monthly_features.rename(columns={3: 'Features'})
monthly_features.reset_index(inplace=True)

In [ ]:
data.head()

In [ ]:
data.iloc[5]

In [ ]:
feature_cleaner(pd.DataFrame(monthly_features['Features']), 4)

In [ ]:
monthly_features['index'][2]

In [ ]:
import os

In [ ]:
data_folder_path = '/home/amin/thesis/src/data/MAIN-FILES/FINNAL_DATA'
feature_folder_path = '/home/amin/thesis/src/Step/Feature_selection_RF'
df_file_list = os.listdir(data_folder_path)
feature_file_list = os.listdir(feature_folder_path)

for file in df_file_list:
    for feature_file in feature_file_list:
        if feature_file == f'RFC_{file}' :
            print(feature_file)

In [ ]:
feature_file_list[0] == f'RFC_{df_file_list[0]}'

In [ ]:
f'RCF_{df_file_list[0]}'

In [ ]:
df_file_list

In [ ]:
feature_file_list

In [ ]:
import os
import warnings

import numpy as np
import pandas as pd
from sklearn.metrics import (accuracy_score, classification_report,
                             confusion_matrix, precision_recall_fscore_support)
from sklearn.model_selection import StratifiedKFold, train_test_split
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.svm import SVC # MODEL

warnings.filterwarnings('ignore')




def return_classifier(df, last_month) :
    def classify_return(return_value):
        """
        Classifies a given return value into different categories based on its magnitude.

        Parameters:
            return_value (numeric): The value to be classified.

        Returns:
            str: The category of the given return value. Possible categories are:
                - 'Above +5' for return values greater than 5.
                - '+2.5 to +5' for return values between 2.5 and 5 (inclusive).
                - '+0 to +2.5' for return values between 0 and 2.5 (inclusive).
                - '0 to -5' for return values between -5 and 0 (inclusive).
                - 'Below -5' for return values less than -5.
        """
        if return_value > 5:
            return 3
        elif 2.5 < return_value <= 5:
            return 2
        elif 0 <= return_value <= 2.5:
            return 1
        elif -5 <= return_value < 0:
            return -1
        else:
            return -2




    pct_price = df['پایانی*سهم*'].pct_change() * 100
    df['Return_Class'] = pct_price.apply(classify_return)
    #df['Return_Class']  = LabelEncoder().fit_transform(df['Return_Class'])
    df['Shifted_Return_Class'] = df['Return_Class'].shift(periods=1).fillna(1)

    scaling = StandardScaler()

    # Select numeric columns except the target column
    numeric_columns = df.select_dtypes(include=[np.number]).drop(columns=['Return_Class']).columns.tolist()
    # Extract the subset of data with only numeric columns
    num_data = df[numeric_columns]
    num_data_last = last_month[numeric_columns]

    y_df = df['Return_Class']
    X_df = scaling.fit_transform(num_data)
    X_last_month = scaling.fit_transform(num_data_last)

     # Train-test split data
    X_train, X_test, y_train, y_test = train_test_split(X_df, y_df, test_size=0.2)


    model = SVC()
    # Fit the model
    model.fit(X_train, y_train)

    # Predict on the test set (either old or new)
    y_pred = model.predict(X_test)

    next_month = model.predict(X_last_month)
    # Evaluation metrics for classification
    accuracy = accuracy_score(y_test, y_pred)
    precision, recall, f1, _ = precision_recall_fscore_support(y_test, y_pred, average= 'macro')

    return accuracy, precision,recall, f1 , next_month



def feature_cleaner(df, inx) :
    """
	This function takes in a DataFrame `df` and an index `inx` as parameters.

	It cleans the features in the DataFrame at the specified index by removing square brackets,
	replacing single quotes with empty strings, and removing leading or trailing spaces.

	If the feature 'پایانی*سهم*' is not already present in the list of cleaned features, it is added.

	If the feature 'پایین\\\\u200cترین*سهم*' is present in the list of cleaned features, it is removed.

	The function returns the cleaned list of features.
	"""
    feat_imp = df.Features[inx].replace("[", "").replace("]", "")
    feat_imp = feat_imp.split(",")
    list_i = [ ]
    for item in feat_imp:
        list_i.append(item.replace("'", ""))
    list2 = [ ]
    for item in list_i :
        if item.startswith(' ') :
            list2.append(item[1: ])
        elif item.endswith(' ') :
            list2.append(item[:-1])
        else :
            list2.append(item)
    if 'پایانی*سهم*' not in list2 :
        list2.append('پایانی*سهم*')

    return list2



data_folder_path = '/home/amin/thesis/src/data/MAIN-FILES/FINNAL_DATA'
feature_folder_path = '/home/amin/thesis/src/Step/Feature_selection_RF'
df_file_list = os.listdir(data_folder_path)
feature_file_list = os.listdir(feature_folder_path)

for file in df_file_list:
    final_result = { }
    for feature_file in feature_file_list:

        if feature_file == f'RFC_{file}' :
            print(feature_file)

            data = pd.read_excel(f'{data_folder_path}/{file}')
            data.drop(columns=['تاریخ شمسی'], inplace=True)
            df = data.resample('M', on='Date').mean()
            df.reset_index(inplace=True)
            df['Date'] = pd.to_datetime(df['Date'])

            feature_df = pd.read_excel(f'{feature_folder_path}/{feature_file}')
            monthly_features = pd.DataFrame(feature_df.iloc[-1],)
            monthly_features = monthly_features.rename(columns={3: 'Features'})
            monthly_features.reset_index(inplace=True)


            for inx in range(5 , len(df)) :
                new_df = df.iloc[ : inx - 1 ]
                last_month = df.iloc[inx]
                imp_columns = feature_cleaner(monthly_features, inx)
                try:
                    final_df = new_df[imp_columns]
                    final_last_month = last_month[imp_columns]
                    accuracy, precision, recall, f1, next_month = return_classifier(final_df, final_last_month)
                except KeyError :
                    except_voc = 'پایین\\\\u200cترین*سهم*'
                    if except_voc in imp_columns :
                        imp_columns.remove(except_voc)
                        final_df = new_df[imp_columns]
                        accuracy, precision, recall, f1, next_month = return_classifier(final_df, final_last_month)
                final_result[f"{monthly_features['index'][inx]}"] = {
                                                                    'Accuracy': accuracy,
                                                                    'Precision': precision,
                                                                    'Recall': recall,
                                                                    'F1': f1,
                                                                    'Next_Month' : next_month,
                                                                    }

        else :
            continue


        final_result = pd.DataFrame(final_result, index=['Accuracy', 'Precision', 'Recall', 'F1', 'Next Month'])
        final_result.to_excel(f'/home/amin/thesis/src/Step2_Classification/SVM/SVM_{file}', index=True)









In [ ]:
import os
import warnings

import numpy as np
import pandas as pd
from sklearn.metrics import (accuracy_score, classification_report,
                             confusion_matrix, precision_recall_fscore_support)
from sklearn.model_selection import StratifiedKFold, train_test_split
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.svm import SVC # MODEL

warnings.filterwarnings('ignore')




def return_classifier(df, final_last_month) :
    def classify_return(return_value):
        """
        Classifies a given return value into different categories based on its magnitude.

        Parameters:
            return_value (numeric): The value to be classified.

        Returns:
            str: The category of the given return value. Possible categories are:
                - 'Above +5' for return values greater than 5.
                - '+2.5 to +5' for return values between 2.5 and 5 (inclusive).
                - '+0 to +2.5' for return values between 0 and 2.5 (inclusive).
                - '0 to -5' for return values between -5 and 0 (inclusive).
                - 'Below -5' for return values less than -5.
        """
        if return_value > 5:
            return 3
        elif 2.5 < return_value <= 5:
            return 2
        elif 0 <= return_value <= 2.5:
            return 1
        elif -5 <= return_value < 0:
            return -1
        else:
            return -2




    pct_price = df['پایانی*سهم*'].pct_change() * 100
    df['Return_Class'] = pct_price.apply(classify_return)
    #df['Return_Class']  = LabelEncoder().fit_transform(df['Return_Class'])
    df['Shifted_Return_Class'] = df['Return_Class'].shift(periods=1).fillna(1)

    scaling = StandardScaler()

    # Select numeric columns except the target column
    numeric_columns = df.select_dtypes(include=[np.number]).drop(columns=['Return_Class']).columns.tolist()
    # Extract the subset of data with only numeric columns
    num_data = df[numeric_columns]
    last_month_num = final_last_month.shape(1,-1)

    y_df = df['Return_Class']
    X_df = scaling.fit_transform(num_data)
    X_last_month = scaling.fit_transform(last_month_num)


     # Train-test split data
    X_train, X_test, y_train, y_test = train_test_split(X_df, y_df, test_size=0.2)


    model = SVC()
    # Fit the model
    model.fit(X_train, y_train)

    # Predict on the test set (either old or new)
    y_pred = model.predict(X_test)
    next_month_prediction = model.predict(X_last_month)

    # Evaluation metrics for classification
    accuracy = accuracy_score(y_test, y_pred)
    precision, recall, f1, _ = precision_recall_fscore_support(y_test, y_pred, average= 'macro')

    return accuracy, precision,recall, f1, next_month_prediction



def feature_cleaner(df, inx) :
    """
	This function takes in a DataFrame `df` and an index `inx` as parameters.

	It cleans the features in the DataFrame at the specified index by removing square brackets,
	replacing single quotes with empty strings, and removing leading or trailing spaces.

	If the feature 'پایانی*سهم*' is not already present in the list of cleaned features, it is added.

	If the feature 'پایین\\\\u200cترین*سهم*' is present in the list of cleaned features, it is removed.

	The function returns the cleaned list of features.
	"""
    feat_imp = df.Features[inx].replace("[", "").replace("]", "")
    feat_imp = feat_imp.split(",")
    list_i = [ ]
    for item in feat_imp:
        list_i.append(item.replace("'", ""))
    list2 = [ ]
    for item in list_i :
        if item.startswith(' ') :
            list2.append(item[1: ])
        elif item.endswith(' ') :
            list2.append(item[:-1])
        else :
            list2.append(item)
    if 'پایانی*سهم*' not in list2 :
        list2.append('پایانی*سهم*')

    return list2



data_folder_path = '/home/amin/thesis/src/data/MAIN-FILES/FINNAL_DATA'
feature_folder_path = '/home/amin/thesis/src/Step/Feature_selection_RF'
df_file_list = os.listdir(data_folder_path)
feature_file_list = os.listdir(feature_folder_path)

for file in df_file_list:
    final_result = { }
    for feature_file in feature_file_list:

        if feature_file == f'RFC_{file}' :
            print(feature_file)

            data = pd.read_excel(f'{data_folder_path}/{file}')
            data.drop(columns=['تاریخ شمسی'], inplace=True)
            df = data.resample('M', on='Date').mean()
            df.reset_index(inplace=True)
            df['Date'] = pd.to_datetime(df['Date'])

            feature_df = pd.read_excel(f'{feature_folder_path}/{feature_file}')
            monthly_features = pd.DataFrame(feature_df.iloc[-1],)
            monthly_features = monthly_features.rename(columns={3: 'Features'})
            monthly_features.reset_index(inplace=True)


            for inx in range(5 , len(df)) :
                new_df = df.iloc[ : inx - 1 ]
                last_month = df.iloc[-1]
                imp_columns = feature_cleaner(monthly_features, inx)
                final_df = new_df[imp_columns]
                final_last_month = last_month[imp_columns]
                accuracy, precision,recall, f1, next_month_prediction = return_classifier(final_df, final_last_month)
                final_result[f"{monthly_features['index'][inx]}"] = {'Accuracy': accuracy,'Precision': precision,'Recall': recall,'F1': f1 ,'Next_Month_Prediction' : next_month_prediction}
        else :
            continue


        final_result = pd.DataFrame(final_result, index=['Accuracy', 'Precision', 'Recall', 'F1', 'Next_Month_Prediction'])
        final_result.to_excel(f'/home/amin/thesis/src/Step2_Classification/SVM/SVM_{file}', index=True)









In [ ]:
data = pd.read_excel('/home/amin/thesis/src/data/MAIN-FILES/FINNAL_DATA/کنور.xlsx')
feature = pd.read_excel('/home/amin/thesis/src/Step/Feature_selection_RF/RFC_کنور.xlsx')

In [ ]:
data.drop(columns=['تاریخ شمسی'], inplace=True)
df = data.resample('M', on='Date').mean()
df.reset_index(inplace=True)
df['Date'] = pd.to_datetime(df['Date'])

In [ ]:
df

In [ ]:
monthly_features = pd.DataFrame(feature.iloc[-1])
monthly_features = monthly_features.rename(columns={3: 'Features'})
monthly_features.reset_index(inplace=True)

In [ ]:
monthly_features

In [ ]:
import os
import warnings

import numpy as np
import pandas as pd
from sklearn.metrics import (accuracy_score, classification_report,
                             confusion_matrix, precision_recall_fscore_support)
from sklearn.model_selection import StratifiedKFold, train_test_split
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.svm import SVC # MODEL

warnings.filterwarnings('ignore')



def classify_return(return_value):
        """
        Classifies a given return value into different categories based on its magnitude.

        Parameters:
            return_value (numeric): The value to be classified.

        Returns:
            str: The category of the given return value. Possible categories are:
                - 'Above +5' for return values greater than 5.
                - '+2.5 to +5' for return values between 2.5 and 5 (inclusive).
                - '+0 to +2.5' for return values between 0 and 2.5 (inclusive).
                - '0 to -5' for return values between -5 and 0 (inclusive).
                - 'Below -5' for return values less than -5.
        """
        if return_value > 5:
            return 3
        elif 2.5 < return_value <= 5:
            return 2
        elif 0 <= return_value <= 2.5:
            return 1
        elif -5 <= return_value < 0:
            return -1
        else:
            return -2




def return_classifier(df, last_month , monthly_features, inx ) :

    scaling = StandardScaler()

    # Select numeric columns except the target column
    numeric_columns = df.select_dtypes(include=[np.number]).drop(columns=['Target']).columns.tolist()
    numeric_columns_last_month = last_month.select_dtypes(include=[np.number]).drop(columns=['Target']).columns.tolist()
     # Extract the subset of data with only numeric columns
    X_df = df[numeric_columns]
    y_df = df['Target']
    last_month_num = last_month[numeric_columns_last_month]


    my_list = feature_cleaner(monthly_features, inx)
    imp_columns = [item for item in my_list if r'\u200' not in item]




    X_df = X_df[imp_columns]
    X_last_month = last_month_num[imp_columns]

    X_df = scaling.fit_transform(X_df)
    X_last_month = scaling.fit_transform(X_last_month)




     # Train-test split data
    X_train, X_test, y_train, y_test = train_test_split(X_df, y_df, test_size=0.2)


    model = SVC()
    # Fit the model
    model.fit(X_train, y_train)

    # Predict on the test set (either old or new)
    y_pred = model.predict(X_test)
    next_month_prediction = model.predict(X_last_month)

    # Evaluation metrics for classification
    accuracy = accuracy_score(y_test, y_pred)
    precision, recall, f1, _ = precision_recall_fscore_support(y_test, y_pred, average= 'macro')

    return accuracy, precision, recall, f1, next_month_prediction



def feature_cleaner(df, inx) :
    """
	This function takes in a DataFrame `df` and an index `inx` as parameters.

	It cleans the features in the DataFrame at the specified index by removing square brackets,
	replacing single quotes with empty strings, and removing leading or trailing spaces.

	If the feature 'پایانی*سهم*' is not already present in the list of cleaned features, it is added.

	If the feature 'پایین\\\\u200cترین*سهم*' is present in the list of cleaned features, it is removed.

	The function returns the cleaned list of features.
	"""
    feat_imp = df.Features[inx].replace("[", "").replace("]", "")
    feat_imp = feat_imp.split(",")
    list_i = [ ]
    for item in feat_imp:
        list_i.append(item.replace("'", ""))
    list2 = [ ]
    for item in list_i :
        if item.startswith(' ') :
            list2.append(item[1: ])
        elif item.endswith(' ') :
            list2.append(item[:-1])
        else :
            list2.append(item)
    if 'پایانی*سهم*' not in list2 :
        list2.append('پایانی*سهم*')

    return list2

In [ ]:
pct_price = df['پایانی*سهم*'].pct_change() * 100
df['Return_Class'] = pct_price.apply(classify_return)
df['Shifted_Return_Class'] = df['Return_Class'].shift(periods=1).fillna(1)
df.rename(columns={'Shifted_Return_Class' : 'Target'}, inplace=True)
df.drop('Return_Class', axis=1, inplace=True)


In [ ]:
final_result = { }
for inx in range(5 , len(df)) :
    new_df = df.iloc[ : inx - 1 ]
    last_month = df.iloc[ inx : inx + 1]



    accuracy, precision, recall, f1, next_month_prediction = return_classifier(df=new_df, last_month= last_month , monthly_features= monthly_features, inx= inx)
    final_result[f"{monthly_features['index'][inx]}"] = {'Accuracy': accuracy,'Precision': precision,'Recall': recall,'F1': f1 ,'Next_Month_Prediction' : next_month_prediction}

In [ ]:
final_result = pd.DataFrame(final_result, index=['Accuracy', 'Precision', 'Recall', 'F1', 'Next_Month_Prediction'])

In [ ]:
final_result

In [19]:
import os
import warnings

import numpy as np
import pandas as pd
from sklearn.metrics import (accuracy_score, classification_report,
                             confusion_matrix, precision_recall_fscore_support)
from sklearn.model_selection import StratifiedKFold, train_test_split
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.svm import SVC # MODEL
from sklearn.model_selection import GridSearchCV
from sklearn.svm import SVC
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import accuracy_score, precision_recall_fscore_support
import numpy as np

from sklearn.metrics import make_scorer, precision_score


warnings.filterwarnings('ignore')

def return_classifier(df, last_month, monthly_features, inx):
    scaling = StandardScaler()

    # Select numeric columns except the target column
    numeric_columns = df.select_dtypes(include=[np.number]).drop(columns=['Target']).columns.tolist()
    numeric_columns_last_month = last_month.select_dtypes(include=[np.number]).drop(columns=['Target']).columns.tolist()
    # Extract the subset of data with only numeric columns
    X_df = df[numeric_columns]
    y_df = df['Target']
    last_month_num = last_month[numeric_columns_last_month]

    my_list = feature_cleaner(monthly_features, inx)
    imp_columns = [item for item in my_list if r'\u200' not in item]

    X_df = X_df[imp_columns]
    X_last_month = last_month_num[imp_columns]

    X_df = scaling.fit_transform(X_df)
    X_last_month = scaling.fit_transform(X_last_month)

    # Train-test split data
    X_train, X_test, y_train, y_test = train_test_split(X_df, y_df, test_size=0.2)

    # Scoring functions for accuracy and precision
    scoring = {
        'accuracy': 'accuracy',
        'precision': make_scorer(precision_score, average='macro')
    }

    # Grid search parameters for SVM
    param_grid = {
        'C': [0.1, 1, 10, 100],
        'gamma': [1, 0.1, 0.01, 0.001],
        'kernel': ['rbf', 'linear', 'poly']
    }

    svm = SVC()
    grid_search = GridSearchCV(svm, param_grid, cv=5, scoring=scoring, refit='precision', n_jobs=-1)
    
    # Fit the model using GridSearch
    grid_search.fit(X_train, y_train)

    # Best parameters from the grid search
    best_params = grid_search.best_params_

    # Using the best parameters to build the model
    best_svm = SVC(**best_params)
    best_svm.fit(X_train, y_train)

    # Predict on the test set (either old or new)
    y_pred = best_svm.predict(X_test)
    next_month_prediction = best_svm.predict(X_last_month)

    # Evaluation metrics for classification
    accuracy = accuracy_score(y_test, y_pred)
    precision, recall, f1, _ = precision_recall_fscore_support(y_test, y_pred, average='macro')

    return accuracy, precision, recall, f1, next_month_prediction


In [10]:
def feature_cleaner(df, inx) :
    """
	This function takes in a DataFrame `df` and an index `inx` as parameters.

	It cleans the features in the DataFrame at the specified index by removing square brackets,
	replacing single quotes with empty strings, and removing leading or trailing spaces.

	If the feature 'پایانی*سهم*' is not already present in the list of cleaned features, it is added.

	The function returns the cleaned list of features.
	"""
    feat_imp = df.Features[inx].replace("[", "").replace("]", "")
    feat_imp = feat_imp.split(",")
    list_i = [ ]
    for item in feat_imp:
        list_i.append(item.replace("'", ""))
    list2 = [ ]
    for item in list_i :
        if item.startswith(' ') :
            list2.append(item[1: ])
        elif item.endswith(' ') :
            list2.append(item[:-1])
        else :
            list2.append(item)
    if 'پایانی*سهم*' not in list2 :
        list2.append('پایانی*سهم*')

    return list2

In [12]:
def classify_return(return_value):
        """
        Classifies a given return value into different categories based on its magnitude.

        Parameters:
            return_value (numeric): The value to be classified.

        Returns:
            str: The category of the given return value. Possible categories are:
                - 'Above +5' for return values greater than 5.
                - '+2.5 to +5' for return values between 2.5 and 5 (inclusive).
                - '+0 to +2.5' for return values between 0 and 2.5 (inclusive).
                - '0 to -5' for return values between -5 and 0 (inclusive).
                - 'Below -5' for return values less than -5.
        """
        if return_value > 5:
            return 3
        elif 2.5 < return_value <= 5:
            return 2
        elif 0 <= return_value <= 2.5:
            return 1
        elif -5 <= return_value < 0:
            return -1
        else:
            return -2


In [12]:
import pandas as pd
import numpy as np

In [13]:
data = pd.read_excel('/home/amin/thesis/src/data/MAIN-FILES/FINNAL_DATA/کنور.xlsx')
feature = pd.read_excel('/home/amin/thesis/src/Step/Feature_selection_RF/RFC_کنور.xlsx')



data.drop(columns=['تاریخ شمسی'], inplace=True)
df = data.resample('M', on='Date').mean()
df.reset_index(inplace=True)
df['Date'] = pd.to_datetime(df['Date'])

monthly_features = pd.DataFrame(feature.iloc[-1])
monthly_features = monthly_features.rename(columns={3: 'Features'})
monthly_features.reset_index(inplace=True)

In [14]:
pct_price = df['پایانی*سهم*'].pct_change() * 100
df['Return_Class'] = pct_price.apply(classify_return)
df['Shifted_Return_Class'] = df['Return_Class'].shift(periods=1).fillna(1)
df.rename(columns={'Shifted_Return_Class' : 'Target'}, inplace=True)
df.drop('Return_Class', axis=1, inplace=True)


In [20]:
final_result = { }
for inx in range(20 , len(df)) :
    new_df = df.iloc[ : inx - 1 ]
    last_month = df.iloc[ inx : inx + 1]



    accuracy, precision, recall, f1, next_month_prediction = return_classifier(df=new_df, last_month= last_month , monthly_features= monthly_features, inx= inx)
    final_result[f"{monthly_features['index'][inx]}"] = {'Accuracy': accuracy,'Precision': precision,'Recall': recall,'F1': f1 ,'Next_Month_Prediction' : next_month_prediction}
final_result = pd.DataFrame(final_result, index=['Accuracy', 'Precision', 'Recall', 'F1', 'Next_Month_Prediction'])
final_result

/home/amin/miniconda3/envs/py310/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/amin/miniconda3/envs/py310/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/amin/miniconda3/envs/py310/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/amin/miniconda3/envs/py310/lib/

2015-5    2015-6    2015-7    2015-8    2015-9  \
Accuracy                  1.0      0.75       0.4       0.8       0.4   
Precision                 1.0     0.375  0.133333       0.4  0.166667   
Recall                    1.0       0.5  0.333333       0.5     0.125   
F1                        1.0  0.428571  0.190476  0.444444  0.142857   
Next_Month_Prediction  [-2.0]    [-2.0]    [-2.0]    [-2.0]    [-2.0]   

                        2015-10 2015-11   2015-12    2016-1    2016-2  ...  \
Accuracy                    0.6     0.6  0.833333       0.5       0.5  ...   
Precision                   0.2     0.3  0.416667  0.166667  0.166667  ...   
Recall                 0.333333     0.5       0.5  0.333333  0.333333  ...   
F1                         0.25   0.375  0.454545  0.222222  0.222222  ...   
Next_Month_Prediction    [-2.0]  [-2.0]    [-2.0]    [-2.0]    [-2.0]  ...   

                        2022-11   2022-12    2023-1    2023-2    2023-3  \
Accuracy               0.363636  0.318182  0.304348  0.434783  0.173913   
Precision              0.305357  0.185714     0.125  0.285714       0.1   
Recall                 0.308333  0.188889  0.173333  0.253333     0.175   
F1                     0.291889  0.186425  0.145055  0.264253  0.116484   
Next_Month_Prediction    [-1.0]     [3.0]     [3.0]    [-1.0]    [-2.0]   

                         2023-4    2023-5    2023-6    2023-7    2023-8  
Accuracy               0.521739  0.347826  0.291667  0.458333     0.375  
Precision                 0.525     0.225  0.144444  0.514286  0.261299  
Recall                 0.424444  0.186111  0.211111  0.340909  0.294286  
F1                     0.457041  0.203361  0.166802  0.365168      0.24  
Next_Month_Prediction    [-2.0]     [3.0]     [3.0]    [-1.0]    [-1.0]  

[5 rows x 100 columns]

In [21]:
final_result

2015-5    2015-6    2015-7    2015-8    2015-9  \
Accuracy                  1.0      0.75       0.4       0.8       0.4   
Precision                 1.0     0.375  0.133333       0.4  0.166667   
Recall                    1.0       0.5  0.333333       0.5     0.125   
F1                        1.0  0.428571  0.190476  0.444444  0.142857   
Next_Month_Prediction  [-2.0]    [-2.0]    [-2.0]    [-2.0]    [-2.0]   

                        2015-10 2015-11   2015-12    2016-1    2016-2  ...  \
Accuracy                    0.6     0.6  0.833333       0.5       0.5  ...   
Precision                   0.2     0.3  0.416667  0.166667  0.166667  ...   
Recall                 0.333333     0.5       0.5  0.333333  0.333333  ...   
F1                         0.25   0.375  0.454545  0.222222  0.222222  ...   
Next_Month_Prediction    [-2.0]  [-2.0]    [-2.0]    [-2.0]    [-2.0]  ...   

                        2022-11   2022-12    2023-1    2023-2    2023-3  \
Accuracy               0.363636  0.318182  0.304348  0.434783  0.173913   
Precision              0.305357  0.185714     0.125  0.285714       0.1   
Recall                 0.308333  0.188889  0.173333  0.253333     0.175   
F1                     0.291889  0.186425  0.145055  0.264253  0.116484   
Next_Month_Prediction    [-1.0]     [3.0]     [3.0]    [-1.0]    [-2.0]   

                         2023-4    2023-5    2023-6    2023-7    2023-8  
Accuracy               0.521739  0.347826  0.291667  0.458333     0.375  
Precision                 0.525     0.225  0.144444  0.514286  0.261299  
Recall                 0.424444  0.186111  0.211111  0.340909  0.294286  
F1                     0.457041  0.203361  0.166802  0.365168      0.24  
Next_Month_Prediction    [-2.0]     [3.0]     [3.0]    [-1.0]    [-1.0]  

[5 rows x 100 columns]

In [16]:
import os
import warnings
from typing import List

import numpy as np
import pandas as pd
from sklearn.metrics import (accuracy_score, make_scorer,
                             precision_recall_fscore_support, precision_score)
from sklearn.model_selection import GridSearchCV, train_test_split
from sklearn.preprocessing import StandardScaler
from xgboost import XGBClassifier  # MODEL

warnings.filterwarnings('ignore')

def return_classifier(df: pd.DataFrame, last_month: pd.DataFrame, monthly_features: list, inx: int) -> tuple:
    scaling = StandardScaler()

    numeric_columns = df.select_dtypes(include=[np.number]).drop(columns=['Target']).columns.tolist()
    numeric_columns_last_month = last_month.select_dtypes(include=[np.number]).drop(columns=['Target']).columns.tolist()

    X_df = df[numeric_columns]
    y_df = df['Target']
    last_month_num = last_month[numeric_columns_last_month]

    my_list = feature_cleaner(monthly_features, inx)
    imp_columns = [item for item in my_list if r'\u200' not in item]

    X_df = X_df[imp_columns]
    X_last_month = last_month_num[imp_columns]

    X_df = scaling.fit_transform(X_df)
    X_last_month = scaling.transform(X_last_month)

    X_train, X_test, y_train, y_test = train_test_split(X_df, y_df, test_size=0.2)
    
    xgb = XGBClassifier(n_estimators=100, max_depth=3, learning_rate=0.1)
    xgb.fit(X_train, y_train)

    y_pred = xgb.predict(X_test)
    next_month_prediction = xgb.predict(X_last_month)

    accuracy = accuracy_score(y_test, y_pred)
    precision, recall, f1, _ = precision_recall_fscore_support(y_test, y_pred, average='weighted')

    return accuracy, precision, recall, f1, next_month_prediction



def feature_cleaner(df: pd.DataFrame, inx: int) -> List[str]:
    """
	This function takes in a DataFrame `df` and an index `inx` as parameters.

	It cleans the features in the DataFrame at the specified index by removing square brackets,
	replacing single quotes with empty strings, and removing leading or trailing spaces.

	If the feature 'پایانی*سهم*' is not already present in the list of cleaned features, it is added.

	The function returns the cleaned list of features.
	"""
    feat_imp = df.Features[inx].replace("[", "").replace("]", "")
    feat_imp = feat_imp.split(",")
    list_i = [ ]
    for item in feat_imp:
        list_i.append(item.replace("'", ""))
    list2 = [ ]
    for item in list_i :
        if item.startswith(' ') :
            list2.append(item[1: ])
        elif item.endswith(' ') :
            list2.append(item[:-1])
        else :
            list2.append(item)
    if 'پایانی*سهم*' not in list2 :
        list2.append('پایانی*سهم*')

    return list2

def classify_return(return_value: float) -> int:
    """
    Classifies a given return value into different categories based on its magnitude.

    Parameters:
        return_value (numeric): The value to be classified.

    Returns:
        int: The category of the given return value. Original categories were:
            - 3 for return values greater than 5.
            - 2 for return values between 2.5 and 5 (inclusive).
            - 1 for return values between 0 and 2.5 (inclusive).
            - 0 for return values less than 0.
    """
    if return_value >= 0:
        return 1
    elif  return_value < 0:
        return 0







data_folder_path = '/home/amin/thesis/src/data/MAIN-FILES/FINNAL_DATA'
feature_folder_path = '/home/amin/thesis/src/Step/Feature_selection_RF'
df_file_list = os.listdir(data_folder_path)
feature_file_list = os.listdir(feature_folder_path)

for file in df_file_list:
    final_result = { }
    for feature_file in feature_file_list:

        if feature_file == f'RFC_{file}' :
            print(feature_file)

            data = pd.read_excel(f'{data_folder_path}/{file}')
            feature = pd.read_excel(f'{feature_folder_path}/{feature_file}')

            # Preprocessing steps
            data.drop(columns=['تاریخ شمسی'], inplace=True)
            df = data.resample('M', on='Date').mean()
            df.reset_index(inplace=True)
            df['Date'] = pd.to_datetime(df['Date'])

            # Select monthly features
            monthly_features = pd.DataFrame(feature.iloc[-1])
            monthly_features = monthly_features.rename(columns={3: 'Features'})
            monthly_features.reset_index(inplace=True)

            # Calculate percentage price change and add return class
            pct_price = df['پایانی*سهم*'].pct_change() * 100
            df['Return_Class'] = pct_price.apply(classify_return)
            df['Shifted_Return_Class'] = df['Return_Class'].shift(periods=1).fillna(1)
            df.rename(columns={'Shifted_Return_Class' : 'Target'}, inplace=True)
            df.drop('Return_Class', axis=1, inplace=True)


            for inx in range(20 , len(df)) :
                new_df = df.iloc[ : inx - 1 ]
                last_month = df.iloc[ inx : inx + 1]


                # Perform return classification and store results
                accuracy, precision, recall, f1, next_month_prediction = return_classifier(df=new_df, last_month= last_month , monthly_features= monthly_features, inx= inx)
                final_result[f"{monthly_features['index'][inx]}"] = {'Accuracy': accuracy,'Precision': precision,'Recall': recall,'F1': f1 ,'Next_Month_Prediction' : next_month_prediction}



            final_result = pd.DataFrame(final_result, index=['Accuracy', 'Precision', 'Recall', 'F1', 'Next_Month_Prediction'])
            final_result.to_excel(f'/home/amin/thesis/src/Step2_Classification/XGB/XGB_{file}', index=True)









RFC_کنور.xlsx


In [2]:
import os
import warnings
from typing import List

import numpy as np
import pandas as pd
from sklearn.metrics import (accuracy_score, make_scorer, precision_score ,
                             precision_recall_fscore_support)
from sklearn.model_selection import (GridSearchCV, StratifiedKFold,
                                     train_test_split)
from sklearn.neural_network import MLPClassifier
from sklearn.preprocessing import StandardScaler

warnings.filterwarnings('ignore')

def return_classifier(df: pd.DataFrame, last_month: pd.DataFrame, monthly_features: list, inx: int) -> tuple:
    scaling = StandardScaler()

    numeric_columns = df.select_dtypes(include=[np.number]).drop(columns=['Target']).columns.tolist()
    numeric_columns_last_month = last_month.select_dtypes(include=[np.number]).drop(columns=['Target']).columns.tolist()

    X_df = df[numeric_columns]
    y_df = df['Target']
    last_month_num = last_month[numeric_columns_last_month]

    my_list = feature_cleaner(monthly_features, inx)
    imp_columns = [item for item in my_list if r'\u200' not in item]

    X_df = X_df[imp_columns]
    X_last_month = last_month_num[imp_columns]

    X_df = scaling.fit_transform(X_df)
    X_last_month = scaling.transform(X_last_month)

    X_train, X_test, y_train, y_test = train_test_split(X_df, y_df, test_size=0.2)

    # Neural Network parameters for grid search
    # param_grid = {
    #     'hidden_layer_sizes': [(100,), (200,), (300,)],
    #     'activation': ['relu', 'tanh'],
    #     'solver': ['adam'],
    #     'alpha': [0.0001, 0.001, 0.01],
    #     'learning_rate': ['constant', 'adaptive'],
    #     'max_iter': [200, 300, 500],
    # }

    ann = MLPClassifier()
    # grid_search = GridSearchCV(ann, param_grid, cv=StratifiedKFold(n_splits=5), scoring=make_scorer(precision_score, average='weighted'), n_jobs=-1)
    # grid_search.fit(X_train, y_train)
    ann.fit(X_train, y_train)

    # best_params = grid_search.best_params_

    # best_ann = MLPClassifier(**best_params)
    # best_ann.fit(X_train, y_train)

    # y_pred = best_ann.predict(X_test)
    y_pred = ann.predict(X_test)

    # next_month_prediction = best_ann.predict(X_last_month)
    next_month_prediction = ann.predict(X_last_month)

    accuracy = accuracy_score(y_test, y_pred)
    precision, recall, f1, _ = precision_recall_fscore_support(y_test, y_pred, average='weighted')

    return accuracy, precision, recall, f1, next_month_prediction


def feature_cleaner(df: pd.DataFrame, inx: int) -> List[str]:
    """
	This function takes in a DataFrame `df` and an index `inx` as parameters.

	It cleans the features in the DataFrame at the specified index by removing square brackets,
	replacing single quotes with empty strings, and removing leading or trailing spaces.

	If the feature 'پایانی*سهم*' is not already present in the list of cleaned features, it is added.

	The function returns the cleaned list of features.
	"""
    feat_imp = df.Features[inx].replace("[", "").replace("]", "")
    feat_imp = feat_imp.split(",")
    list_i = [ ]
    for item in feat_imp:
        list_i.append(item.replace("'", ""))
    list2 = [ ]
    for item in list_i :
        if item.startswith(' ') :
            list2.append(item[1: ])
        elif item.endswith(' ') :
            list2.append(item[:-1])
        else :
            list2.append(item)
    if 'پایانی*سهم*' not in list2 :
        list2.append('پایانی*سهم*')

    return list2

def classify_return(return_value: float) -> int:
        """
        Classifies a given return value into different categories based on its magnitude.

        Parameters:
            return_value (numeric): The value to be classified.

        Returns:
            str: The category of the given return value. Possible categories are:
                - '3' for return values greater than 5.
                - '2' for return values between 2.5 and 5 (inclusive).
                - '1' for return values between 0 and 2.5 (inclusive).
                - '-1' for return values between -5 and 0 (inclusive).
                - '-2' for return values less than -5.
        """
        if return_value > 5:
            return 3
        elif 2.5 < return_value <= 5:
            return 2
        elif 0 <= return_value <= 2.5:
            return 1
        elif -5 <= return_value < 0:
            return -1
        else:
            return -2




data_folder_path = '/home/amin/thesis/src/data/MAIN-FILES/FINNAL_DATA'
feature_folder_path = '/home/amin/thesis/src/Step/Feature_selection_RF'
df_file_list = os.listdir(data_folder_path)
feature_file_list = os.listdir(feature_folder_path)

for file in df_file_list:
    final_result = { }
    for feature_file in feature_file_list:

        if feature_file == f'RFC_{file}' :
            print(feature_file)

            data = pd.read_excel(f'{data_folder_path}/{file}')
            feature = pd.read_excel(f'{feature_folder_path}/{feature_file}')

            # Preprocessing steps
            data.drop(columns=['تاریخ شمسی'], inplace=True)
            df = data.resample('M', on='Date').mean()
            df.reset_index(inplace=True)
            df['Date'] = pd.to_datetime(df['Date'])

            # Select monthly features
            monthly_features = pd.DataFrame(feature.iloc[-1])
            monthly_features = monthly_features.rename(columns={3: 'Features'})
            monthly_features.reset_index(inplace=True)

            # Calculate percentage price change and add return class
            pct_price = df['پایانی*سهم*'].pct_change() * 100
            df['Return_Class'] = pct_price.apply(classify_return)
            df['Shifted_Return_Class'] = df['Return_Class'].shift(periods=1).fillna(1)
            df.rename(columns={'Shifted_Return_Class' : 'Target'}, inplace=True)
            df.drop('Return_Class', axis=1, inplace=True)


            for inx in range(20 , len(df)) :
                new_df = df.iloc[ : inx - 1 ]
                last_month = df.iloc[ inx : inx + 1]


                # Perform return classification and store results
                accuracy, precision, recall, f1, next_month_prediction = return_classifier(df=new_df, last_month= last_month , monthly_features= monthly_features, inx= inx)
                final_result[f"{monthly_features['index'][inx]}"] = {'Accuracy': accuracy,'Precision': precision,'Recall': recall,'F1': f1 ,'Next_Month_Prediction' : next_month_prediction}



            final_result = pd.DataFrame(final_result, index=['Accuracy', 'Precision', 'Recall', 'F1', 'Next_Month_Prediction'])
            final_result.to_excel(f'/home/amin/thesis/src/Step2_Classification/ANN/ANN_{file}', index=True)









RFC_کنور.xlsx
